This notebook takes ~10 seconds to run.

There are interactive scatter plots and search function (also online) for you to play with. 

Have fun.

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pickle

with open("./../models/final_model.pkl", "rb") as f:
    data = pickle.load(f)
model = data["model"]

with open("./../models/StandardScalers.pkl", "rb") as f:
    data = pickle.load(f)
SS_y = data["SS_y"]

df = pd.read_parquet("./../data/steam_game_dataset.parquet")
df_conf_tier = pd.read_parquet('./../data/df_conf_tier_v1.parquet')
df_X_z = pd.read_parquet('./../data/df_X_z_v1.parquet')

all_X = df_X_z.to_numpy(dtype="float32")
y_pred = SS_y.inverse_transform(model.predict(all_X).reshape(-1, 1)).squeeze(-1)

conf_map = {1: "low", 2: "medium", 3: "high", 4: "very high"}

df_results = pd.DataFrame({
    "app_id": df['AppID'],
    "name": df['Name'],
    "metacritic_score": df['Metacritic score'].astype(float),
    "pred_score": y_pred,
    "conf_tier": df_conf_tier['tier_label'],
    "conf_label": df_conf_tier['tier_label'].replace(conf_map)}
    ).sort_values(["conf_tier","metacritic_score","pred_score"],ascending=[False,False,False])



# Show results

## Let's see if we can find hidden gems!

### Games with no Metacritic score, but has a high predicted score with high confidence, are printed in the table below, ordered by predicted score (going across).


In [2]:
import math

mask = (df_results["conf_tier"]==4) & (df_results["metacritic_score"]<=0)
# build the per-row cell text
cells = [
    f"{t}<br>{s:.1f}"
    for t, s in zip(df_results.loc[mask,"name"], 
                       df_results.loc[mask,"pred_score"])
]

n_cols = 4
n_rows = math.ceil(len(cells) / n_cols)

# pad to fill the last row if needed
cells += [""] * (n_rows * n_cols - len(cells))

table = pd.DataFrame(
    np.array(cells).reshape(n_rows, n_cols)
)
display(
    table.style.set_properties(**{"white-space": "pre-line"})
)

print(table.to_string(index_names=False, header=False))

0     Total War: MEDIEVAL II – Definitive Edition<br>87.3               STAR WARS™ - Knights of the Old Republic™<br>86.6                                   FINAL FANTASY VII<br>85.9                                                          Half-Life: Opposing Force<br>85.6
1            STAR WARS™ Empire at War - Gold Pack<br>85.6             Warhammer® 40,000: Dawn of War® - Soulstorm<br>85.1                   Halo: The Master Chief Collection<br>85.0                                                      Commandos: Behind Enemy Lines<br>84.8
2                Marvel's Guardians of the Galaxy<br>84.7                                          Sea of Thieves<br>84.7                           Assassin's Creed® Origins<br>84.6                                                          Assassin's Creed® Odyssey<br>84.6
3                                    Superliminal<br>84.4                                           Ultimate Doom<br>84.3                       Hotline Miami 2: Wrong Number<br>84.3

# Visualization

## In the interactive scatter plots below, you can check out predicted scores of games with (cloud on the right) and without (cloud on the left) a Metacritic score.

In [3]:
import plotly.express as px

def plot_px_scatter(ct,cname,t):
    df = df_results.copy()
    mask = df["metacritic_score"] == 0
    df.loc[mask, "metacritic_score"] += np.random.uniform(-20, 0, size=mask.sum())
    fig = px.scatter(
        df.loc[df["conf_tier"]==ct],
        x="metacritic_score",
        y="pred_score",
        color="conf_label",
        color_discrete_sequence=[cname],
        hover_data=["name","app_id"],
        labels={"metacritic_score": "Metacritic score",
                "pred_score": "Predicted score",
                "conf_label": "Confidence level",
                "name": "Game title"},
        title=(t+"\n(games without true scores get a random negative x value)"),
        width=800, height=600)
    fig.show()
    # fig.write_html(f"./../interactives/{t.lower().replace(' ', '_')}.html")
    

plot_px_scatter(4,"magenta","Very high confidence")
plot_px_scatter(3,"orange","High confidence")
plot_px_scatter(2,"blue","Medium confidence")
plot_px_scatter(1,"gray","Low confidence")


# Search games

## Scroll down to the bottom to search for games in the dataframe.

In [4]:
import re

def search_rows(df,col,q,
    fuzzy_threshold=80,fuzzy_topk=50):
    
    s = df[col].astype("string")

    if q is None or str(q).strip() == "":
        return df.iloc[0:0]  # empty result

    from rapidfuzz import process, fuzz

    choices = s.fillna("").tolist()
    hits = process.extract(q, choices, scorer=fuzz.WRatio, limit=fuzzy_topk)
    keep = [(match, score, idx) for (match, score, idx) in hits if score >= fuzzy_threshold]
    if not keep:
        return df.iloc[0:0]
    idxs = [k[2] for k in keep]
    scores = [k[1] for k in keep]
    # return df.iloc[idxs].assign(_fuzzy_score=scores)
    return df.iloc[idxs]


In [5]:
# df_results.to_parquet('./../data/df_results.parquet',compression='gzip')

In [6]:
# put your search keyword here
searchname = "stardew valley"


matches = search_rows(df_results, "name", searchname,fuzzy_threshold=78)

pd.options.display.float_format = "{:.1f}".format
matches

app_id            name  metacritic_score  pred_score  conf_tier  \
60445  413150  Stardew Valley              89.0        81.6        4.0   
25140  378610          Valley               0.0        75.4        4.0   

      conf_label  
60445  very high  
25140  very high